In [2]:
import re
import pandas as pd
import os
import json

# clear the data from scanners

In [3]:
tags = json.load(open("../data/03_list_tags/tags_flat_3000.json"))
len(tags)

3207

# clear clair

In [4]:
def get_v(tag: str):
    """
    get result of scan for specific tag
    """
    clair_folder = "../data/04_scan/clair/res"
    filename = tag.replace(":", "_").replace("/", "_") + ".json"
    filepath = os.path.join(clair_folder, filename)
    if os.path.exists(filepath):
        res = json.load(open(filepath))
        return res
    print(f"{tag} not exists")

In [5]:
def get_cve_ids(v):
    # get cve id
    cve_re = r"CVE-\d{4}-\d+"
    ghsa_re = r"GHSA-[a-z0-9]{4}-[a-z0-9]{4}-[a-z0-9]{4}"
    sas = []

    # search cve in name
    if re.search(cve_re, v["name"]):
        sas.append(re.findall(cve_re, v["name"])[0])
    else:
        # search rhsa in name
        if re.search(ghsa_re, v["name"]):
            sas.append(re.findall(ghsa_re, v["name"])[0])

        # search cve in links
        if re.search(cve_re, v["links"]):
            sas.extend(re.findall(cve_re, v["links"]))
        else:
            # search rhsa in links
            if re.search(ghsa_re, v["links"]):
                ghsas = re.findall(ghsa_re, v["links"])


    sas = set(sas)
    sas.discard("")
    sas = list(sas)
    # print(sas)
    return sas

In [6]:
def get_severity(v):
    severity = v["normalized_severity"].lower()
    return severity

In [7]:
def get_package(v):
    package = v["package"].get("name", "")
    return package

In [8]:
def get_distro(v):
    distro = v["distribution"].get("cpe")
    return distro

In [9]:
def get_fixed(v):
    if v.get("fixed_in_version"):
        return True
    return False

In [10]:
error_tags = []
tags_with_res = {}

for tag in tags:
    tag_res = []
    tag_data = get_v(tag)
    if tag_data:
        for key in tag_data["vulnerabilities"]:
            v = tag_data["vulnerabilities"][key]
            res = {
                "sas": get_cve_ids(v),
                "severity": get_severity(v),
                "package": get_package(v),
                "distro": get_distro(v),
                "fixed": get_fixed(v),
            }
            if len(res["sas"]) > 0:
                tag_res.append(res)
            tags_with_res[tag] = tag_res
            if len(res["sas"]) > 1:
                print(tag, res["sas"])
    else:
        error_tags.append(tag)

stakater/reloader:SNAPSHOT-PR-573-UBI-b599ad5e ['CVE-2023-28322', 'CVE-2023-46218', 'CVE-2023-38546']
stakater/reloader:SNAPSHOT-PR-573-UBI-b599ad5e ['CVE-2023-28322', 'CVE-2023-46218', 'CVE-2023-38546']
stakater/reloader:SNAPSHOT-PR-573-UBI-b599ad5e ['CVE-2023-28322', 'CVE-2023-46218', 'CVE-2023-38546']
stakater/reloader:SNAPSHOT-PR-573-UBI-b599ad5e ['CVE-2023-28322', 'CVE-2023-46218', 'CVE-2023-38546']
istio/pilot:1.18.4-debug ['GHSA-pvcr-v8j8-j5q3', 'CVE-2024-21664']
istio/pilot:1.18.4-debug ['GHSA-jw44-4f3j-q396', 'CVE-2019-25210']
istio/pilot:1.19.4-debug ['GHSA-pvcr-v8j8-j5q3', 'CVE-2024-21664']
istio/pilot:1.13.9-debug ['CVE-2022-41721', 'GHSA-fxg5-wq6x-vr4w']
istio/pilot:1.13.9-debug ['CVE-2023-25165', 'GHSA-pwcw-6f5g-gxf8']
istio/pilot:1.13.9-debug ['GHSA-jw44-4f3j-q396', 'CVE-2019-25210']
istio/pilot:1.13.9-debug ['GHSA-vpvm-3wq2-2wvm', 'CVE-2023-27561']
istio/pilot:1.13.9-debug ['GHSA-pvcr-v8j8-j5q3', 'CVE-2024-21664']
istio/pilot:1.13.9-debug ['GHSA-232p-vwff-86mp', 'CVE-20

In [ ]:
with open("../final_results/clair_tags_vulns.json", "w") as f:
    json.dump(tags_with_res, f, indent=4)

In [ ]:
tags_with_res_flat = []

for tag in tags_with_res:
    for cve in tags_with_res[tag]:
        cve["tag"] = tag
        tags_with_res_flat.append(cve)

In [ ]:
with open("../final_results/clair_tags_vulns_flat.json", "w") as f:
    json.dump(tags_with_res_flat, f, indent=4)

# clear gc

In [62]:
def get_v(tag):
    folder = "../data/04_scan/gc/res"
    filename = tag.replace(":", "_").replace("/", "_") + ".json"
    filepath = os.path.join(folder, filename)
    if os.path.exists(filepath):
        res = json.load(open(filepath))
        return res
    print(f"{tag} not exists")

In [63]:
tag = "datadog/agent:7.38.0-rc.4-jmx"

In [64]:
v = get_v(tag)
print(json.dumps(v, indent=4))

{
    "discovery_summary": {
        "discovery": [
            {
                "createTime": "2024-05-03T09:39:04.021044Z",
                "discovery": {
                    "analysisCompleted": {
                        "analysisType": [
                            "OS",
                            "GO",
                            "MAVEN",
                            "PYPI",
                            "NPM",
                            "NUGET",
                            "RUBYGEMS",
                            "COMPOSER",
                            "RUST"
                        ]
                    },
                    "analysisStatus": "FINISHED_SUCCESS",
                    "continuousAnalysis": "ACTIVE",
                    "lastScanTime": "2024-05-03T17:19:13.530795179Z"
                },
                "kind": "DISCOVERY",
                "name": "projects/skilful-display-422117/occurrences/c7d02e17-d483-43d7-9b78-dc9c8f38b9ba",
                "noteName": "projects

In [65]:
def get_cve_ids(v):
    # get cve id
    cve_re = r"CVE-\d{4}-\d+"
    rhsa_re = r"RHSA-\d{4}-\d+"
    ghsa_re = r"GHSA-[a-z0-9]{4}-[a-z0-9]{4}-[a-z0-9]{4}"

    # name
    name = v.get("vulnerability").get("shortDescription")
    cve_id, rhsa_id, ghsa_id = "", "", ""
    cves, rhsas, ghsas = [], [], []
    if re.search(cve_re, name):
        cve_id = re.findall(cve_re, name)[0]
    elif re.search(rhsa_re, name):
        rhsa_id = re.findall(rhsa_re, name)[0]
    elif re.search(ghsa_re, name):
        ghsa_id = re.findall(ghsa_re, name)[0]
    # print("id:", cve_id, rhsa_id, ghsa_id)

    # other
    other = str(v)
    if re.search(cve_re, other):
        cves = re.findall(cve_re, other)
    elif re.search(rhsa_re, other):
        rhsas = re.findall(rhsa_re, other)
    elif re.search(ghsa_re, other):
        ghsas = re.findall(ghsa_re, other)

    # print("sas:", cves, rhsas, ghsas)

    if len(set(cves)) == 1:
        if cve_id == "":
            cve_id = cves[0]

    if len(set(rhsas)) == 1:
        if rhsa_id == "":
            rhsa_id = rhsas[0]

    if len(set(ghsas)) == 1:
        if ghsa_id == "":
            ghsa_id = ghsas[0]

    id = cve_id or rhsa_id or ghsa_id
    sas = [cve_id, rhsa_id, ghsa_id]
    sas.extend(cves)
    sas.extend(rhsas)
    sas.extend(ghsas)
    sas = set(sas)
    sas.discard("")
    sas = list(sas)
    # print(id, cve_id, sas)
    return id, cve_id, sas

In [66]:
def get_severity(v):
    severity = v.get("vulnerability").get("severity").lower()
    # package = v.get("vulnerability").get("packageIssue")
    # if len(package) > 0:
    #     return package[0].get("affectedPackage")
    # return severity

In [67]:
def get_package(v):
    package = v.get("vulnerability").get("packageIssue")
    if len(package) > 0:
        return package[0].get("affectedPackage")
        return package[0].get("packageType")

In [68]:
def get_distro(v):
    package = v.get("vulnerability").get("packageIssue")
    if len(package) > 0:
        return package[0].get("affectedCpeUri")

In [69]:
def get_fixed(v):
    return v.get("vulnerability").get("fixAvailable", False)

In [70]:
error_tags = []
tags_with_res = {}

for tag in tags:
    tag_res = []
    tag_data = get_v(tag)
    if tag_data:
        vulnerabilities = tag_data.get("package_vulnerability_summary", {}).get("vulnerabilities", {})
        for level in vulnerabilities:
            for v in vulnerabilities[level]:
                id, cve_id, sas = get_cve_ids(v)
                res = {
                    "id": id,
                    "cve_id": cve_id,
                    "sas": sas,
                    "severity": level.lower() if level != "None" else "unknown",
                    "package": get_package(v),
                    "distro": get_distro(v),
                    "fixed": get_fixed(v),
                }
                if len(sas) > 0:
                    tag_res.append(res)
        tags_with_res[tag] = tag_res
    else:
        error_tags.append(tag)

mattermost/mattermost-team-edition:1d5b47a not exists
mattermost/mattermost-team-edition:5ce0c57 not exists
mprasil/bitwarden:latest not exists
kubernetes/pause:10.11.6-x86_64 not exists
kubernetes/pause:10.11.4 not exists
kubernetes/pause:10.11.2 not exists
minio/console:v0.15.2 not exists
minio/console:v0.26.1 not exists
minio/console:v0.17.1 not exists


In [ ]:
with open("../final_results/gc_tags_vulns.json", "w") as f:
    json.dump(tags_with_res, f, indent=4)

In [ ]:
tags_with_res_flat = []

for tag in tags_with_res:
    for cve in tags_with_res[tag]:
        cve["tag"] = tag
        tags_with_res_flat.append(cve)

In [ ]:
with open("../final_results/gc_tags_vulns_flat.json", "w") as f:
    json.dump(tags_with_res_flat, f, indent=4)

In [ ]:
pd.DataFrame.from_dict(tags_with_res_flat[:10000]).to_clipboard(excel=True)

# clear grype

In [ ]:
def get_v(tag):
    folder = "../data/04_scan/grype/res"
    filename = tag.replace(":", "_").replace("/", "_") + ".json"
    filepath = os.path.join(folder, filename)
    if os.path.exists(filepath):
        res = json.load(open(filepath))
        return res
    print(f"{tag} not exists")

In [ ]:
tag = "datadog/agent:7.38.0-rc.4-jmx"

In [ ]:
v = get_v(tag)
print(json.dumps(v, indent=4))

In [ ]:
def get_cve_ids(v):
    # get cve id
    cve_re = r"CVE-\d{4}-\d+"
    rhsa_re = r"RHSA-\d{4}-\d+"
    ghsa_re = r"GHSA-[a-z0-9]{4}-[a-z0-9]{4}-[a-z0-9]{4}"

    # name
    name = v.get("vulnerability").get("id")
    cve_id, rhsa_id, ghsa_id = "", "", ""
    cves, rhsas, ghsas = [], [], []
    if re.search(cve_re, name):
        cve_id = re.findall(cve_re, name)[0]
    elif re.search(rhsa_re, name):
        rhsa_id = re.findall(rhsa_re, name)[0]
    elif re.search(ghsa_re, name):
        ghsa_id = re.findall(ghsa_re, name)[0]
    # print("id:", cve_id, rhsa_id, ghsa_id)

    # other
    other = str(v)
    if re.search(cve_re, other):
        cves = re.findall(cve_re, other)
    elif re.search(rhsa_re, other):
        rhsas = re.findall(rhsa_re, other)
    elif re.search(ghsa_re, other):
        ghsas = re.findall(ghsa_re, other)

    # print("sas:", cves, rhsas, ghsas)

    if len(set(cves)) == 1:
        if cve_id == "":
            cve_id = cves[0]

    if len(set(rhsas)) == 1:
        if rhsa_id == "":
            rhsa_id = rhsas[0]

    if len(set(ghsas)) == 1:
        if ghsa_id == "":
            ghsa_id = ghsas[0]

    id = cve_id or rhsa_id or ghsa_id
    sas = [cve_id, rhsa_id, ghsa_id]
    sas.extend(cves)
    sas.extend(rhsas)
    sas.extend(ghsas)
    sas = set(sas)
    sas.discard("")
    sas = list(sas)
    # print(id, cve_id, sas)
    return id, cve_id, sas

In [ ]:
def get_severity(v):
    severity = v.get("vulnerability").get("severity", "unknown").lower()
    return severity

In [ ]:
def get_package(v):
    package = v.get("artifact").get("name")
    return package

In [ ]:
def get_distro(v):
    distro = v.get("distro").get("name")
    version = v.get("distro").get("version")
    return distro, version

In [ ]:
def get_fixed(v):
    if v.get("vulnerability").get("fix").get("state") == "fixed":
        return True
    return False

In [ ]:
error_tags = []
tags_with_res = {}

for tag in tags:
    tag_res = []
    tag_data = get_v(tag)
    if tag_data:
        distro = get_distro(tag_data)

        for v in tag_data["matches"]:
            id, cve_id, sas = get_cve_ids(v)
            res = {
                "id": id,
                "cve_id": cve_id,
                "sas": sas,
                "severity": get_severity(v),
                "package": get_package(v),
                "distro": distro,
                "fixed": get_fixed(v),
            }
            if len(sas) > 0:
                tag_res.append(res)
        tags_with_res[tag] = tag_res
    else:
        error_tags.append(tag)

In [ ]:
with open("../final_results/grype_tags_vulns.json", "w") as f:
    json.dump(tags_with_res, f, indent=4)

In [ ]:
tags_with_res_flat = []

for tag in tags_with_res:
    for cve in tags_with_res[tag]:
        cve["tag"] = tag
        tags_with_res_flat.append(cve)

In [ ]:
with open("../final_results/grype_tags_vulns_flat.json", "w") as f:
    json.dump(tags_with_res_flat, f, indent=4)

In [ ]:
pd.DataFrame.from_dict(tags_with_res_flat[:10000]).to_clipboard(excel=True)

# clear scout

In [ ]:
def get_v(tag):
    folder = "../data/04_scan/scout/res"
    filename = tag.replace(":", "_").replace("/", "_") + ".json"
    filepath = os.path.join(folder, filename)
    if os.path.exists(filepath):
        res = json.load(open(filepath))
        return res
    print(f"{tag} not exists")

In [ ]:
tag = "datadog/agent:7.38.0-rc.4-jmx"

In [ ]:
v = get_v(tag)
print(json.dumps(v, indent=4))

In [ ]:
def get_cve_ids(v):
    # get cve id
    cve_re = r"CVE-\d{4}-\d+"
    rhsa_re = r"RHSA-\d{4}-\d+"
    ghsa_re = r"GHSA-[a-z0-9]{4}-[a-z0-9]{4}-[a-z0-9]{4}"

    # name
    name = v.get("ruleId")
    cve_id, rhsa_id, ghsa_id = "", "", ""
    cves, rhsas, ghsas = [], [], []
    if re.search(cve_re, name):
        cve_id = re.findall(cve_re, name)[0]
    elif re.search(rhsa_re, name):
        rhsa_id = re.findall(rhsa_re, name)[0]
    elif re.search(ghsa_re, name):
        ghsa_id = re.findall(ghsa_re, name)[0]
    # print("id:", cve_id, rhsa_id, ghsa_id)

    # other
    other = str(v)
    if re.search(cve_re, other):
        cves = re.findall(cve_re, other)
    elif re.search(rhsa_re, other):
        rhsas = re.findall(rhsa_re, other)
    elif re.search(ghsa_re, other):
        ghsas = re.findall(ghsa_re, other)

    # print("sas:", cves, rhsas, ghsas)

    if len(set(cves)) == 1:
        if cve_id == "":
            cve_id = cves[0]

    if len(set(rhsas)) == 1:
        if rhsa_id == "":
            rhsa_id = rhsas[0]

    if len(set(ghsas)) == 1:
        if ghsa_id == "":
            ghsa_id = ghsas[0]

    id = cve_id or rhsa_id or ghsa_id
    sas = [cve_id, rhsa_id, ghsa_id]
    sas.extend(cves)
    sas.extend(rhsas)
    sas.extend(ghsas)
    sas = set(sas)
    sas.discard("")
    sas = list(sas)
    # print(id, cve_id, sas)
    return id, cve_id, sas

In [ ]:
def get_severity(v):
    severity = v.get("properties").get("cvssV3_severity").lower()
    return severity

In [ ]:
def get_package(v):
    package = v.get("properties").get("purls")
    return package

In [ ]:
def get_distro(v):
    distro = v.get("distro").get("name")
    version = v.get("distro").get("version")
    return distro, version

In [ ]:
def get_fixed(v):
    if v.get("properties").get("fixed_version"):
        return True
    return False

In [ ]:
error_tags = []
tags_with_res = {}
counter = 0
for tag in tags:
    tag_res = []
    tag_data = get_v(tag)
    if tag_data:
        results = tag_data["runs"][0]["results"]
        rules = tag_data["runs"][0]["tool"]["driver"]["rules"]
        for v in results:
            rule = rules[v["ruleIndex"]]
            id, cve_id, sas = get_cve_ids(v)
            res = {
                "id": id,
                "cve_id": cve_id,
                "sas": sas,
                "severity": get_severity(rule),
                "package": get_package(rule),
                "distro": "",
                "fixed": get_fixed(rule),
            }
            if len(sas) > 0:
                tag_res.append(res)
        tags_with_res[tag] = tag_res
    else:
        error_tags.append(tag)
    counter += 1
    if counter % 100 == 0:
        print(counter)

In [ ]:
with open("../final_results/scout_tags_vulns.json", "w") as f:
    json.dump(tags_with_res, f, indent=4)

In [ ]:
tags_with_res_flat = []

for tag in tags_with_res:
    for cve in tags_with_res[tag]:
        cve["tag"] = tag
        tags_with_res_flat.append(cve)

In [ ]:
with open("../final_results/scout_tags_vulns_flat.json", "w") as f:
    json.dump(tags_with_res_flat, f, indent=4)

In [ ]:
with open("../final_results/scout_tags_vulns_flat.json", "r") as f:
    tags_with_res_flat = json.load(f)

In [ ]:
pd.DataFrame.from_dict(tags_with_res_flat[:10000]).to_clipboard(excel=True)

# clear snyk

In [ ]:
def get_v(tag):
    folder = "../data/04_scan/snyk/res"
    filename = tag.replace(":", "_").replace("/", "_") + ".json"
    filepath = os.path.join(folder, filename)
    if os.path.exists(filepath):
        res = json.load(open(filepath))
        return res
    print(f"{tag} not exists")

In [ ]:
tag = "stakater/reloader:SNAPSHOT-PR-573-UBI-85ed69c2"

In [ ]:
v = get_v(tag)
print(json.dumps(v, indent=4))

In [ ]:
def get_cve_ids(v):
    # get cve id
    cve_re = r"CVE-\d{4}-\d+"
    rhsa_re = r"RHSA-\d{4}-\d+"
    ghsa_re = r"GHSA-[a-z0-9]{4}-[a-z0-9]{4}-[a-z0-9]{4}"

    # name
    name = v.get("ruleId")
    cve_id, rhsa_id, ghsa_id = "", "", ""
    cves, rhsas, ghsas = [], [], []
    # if re.search(cve_re, name):
    #     cve_id = re.findall(cve_re, name)[0]
    # elif re.search(rhsa_re, name):
    #     rhsa_id = re.findall(rhsa_re, name)[0]
    # elif re.search(ghsa_re, name):
    #     ghsa_id = re.findall(ghsa_re, name)[0]
    # print("id:", cve_id, rhsa_id, ghsa_id)

    # other
    other = str(v)
    if re.search(cve_re, other):
        cves = re.findall(cve_re, other)
    elif re.search(rhsa_re, other):
        rhsas = re.findall(rhsa_re, other)
    elif re.search(ghsa_re, other):
        ghsas = re.findall(ghsa_re, other)

    # print("sas:", cves, rhsas, ghsas)

    if len(set(cves)) == 1:
        if cve_id == "":
            cve_id = cves[0]

    if len(set(rhsas)) == 1:
        if rhsa_id == "":
            rhsa_id = rhsas[0]

    if len(set(ghsas)) == 1:
        if ghsa_id == "":
            ghsa_id = ghsas[0]

    id = cve_id or rhsa_id or ghsa_id
    sas = [cve_id, rhsa_id, ghsa_id]
    sas.extend(cves)
    sas.extend(rhsas)
    sas.extend(ghsas)
    sas = set(sas)
    sas.discard("")
    sas = list(sas)
    # print(id, cve_id, sas)
    return id, cve_id, sas

In [ ]:
def get_severity(v):
    severity = v.get("properties").get("cvssv3_baseScore")
    return severity

In [ ]:
def get_package(v):
    package = v.get("locations")[0].get("logicalLocations")[0].get("fullyQualifiedName")
    return package

In [ ]:
def get_distro(v):
    distro = v.get("distro").get("name")
    version = v.get("distro").get("version")
    return distro, version

In [ ]:
def get_fixed(v):
    if v.get("fixes"):
        return True
    return False

In [ ]:
error_tags = []
tags_with_res = {}
counter = 0
for tag in tags:
    tag_res = []
    tag_data = get_v(tag)
    if tag_data:
        for run in tag_data["runs"]:
            results = run["results"]
            rules = run["tool"]["driver"]["rules"]
            for v in results:
                rule_id = v["ruleId"]
                rule = next(r for r in rules if r["id"] == rule_id)

                id, cve_id, sas = get_cve_ids(rule)
                # print(tag)
                # print(id)
                res = {
                    "id": id,
                    "cve_id": cve_id,
                    "sas": sas,
                    "severity": get_severity(rule),
                    "package": get_package(v),
                    "distro": "",
                    "fixed": get_fixed(v),
                }
                if len(sas) > 0:
                    tag_res.append(res)
        tags_with_res[tag] = tag_res
    else:
        error_tags.append(tag)
    counter += 1
    if counter % 100 == 0:
        print(counter)

In [ ]:
with open("../final_results/snyk_tags_vulns.json", "w") as f:
    json.dump(tags_with_res, f, indent=4)

In [ ]:
tags_with_res_flat = []

for tag in tags_with_res:
    for cve in tags_with_res[tag]:
        cve["tag"] = tag
        tags_with_res_flat.append(cve)

In [ ]:
with open("../final_results/snyk_tags_vulns_flat.json", "w") as f:
    json.dump(tags_with_res_flat, f, indent=4)

In [ ]:
pd.DataFrame.from_dict(tags_with_res_flat[:10000]).to_clipboard(excel=True)

# clear trivy

In [6]:
def get_v(tag):
    folder = "../data/04_scan/trivy/res"
    filename = tag.replace(":", "_").replace("/", "_") + ".json"
    filepath = os.path.join(folder, filename)
    if os.path.exists(filepath):
        res = json.load(open(filepath))
        return res
    print(f"{tag} not exists")

In [7]:
tag = "stakater/reloader:SNAPSHOT-PR-573-UBI-85ed69c2"

In [8]:
v = get_v(tag)
print(json.dumps(v, indent=4))

{
    "version": "2.1.0",
    "$schema": "https://raw.githubusercontent.com/oasis-tcs/sarif-spec/master/Schemata/sarif-schema-2.1.0.json",
    "runs": [
        {
            "tool": {
                "driver": {
                    "fullName": "Trivy Vulnerability Scanner",
                    "informationUri": "https://github.com/aquasecurity/trivy",
                    "name": "Trivy",
                    "rules": [
                        {
                            "id": "CVE-2019-12900",
                            "name": "OsPackageVulnerability",
                            "shortDescription": {
                                "text": "bzip2: out-of-bounds write in function BZ2_decompress"
                            },
                            "fullDescription": {
                                "text": "BZ2_decompress in decompress.c in bzip2 through 1.0.6 has an out-of-bounds write when there are many selectors."
                            },
                          

In [10]:
def get_cve_ids(v):
    # get cve id
    cve_re = r"CVE-\d{4}-\d+"
    rhsa_re = r"RHSA-\d{4}-\d+"
    ghsa_re = r"GHSA-[a-z0-9]{4}-[a-z0-9]{4}-[a-z0-9]{4}"

    # name
    name = v.get("ruleId")
    cve_id, rhsa_id, ghsa_id = "", "", ""
    cves, rhsas, ghsas = [], [], []
    if re.search(cve_re, name):
        cve_id = re.findall(cve_re, name)[0]
    elif re.search(rhsa_re, name):
        rhsa_id = re.findall(rhsa_re, name)[0]
    elif re.search(ghsa_re, name):
        ghsa_id = re.findall(ghsa_re, name)[0]
    # print("id:", cve_id, rhsa_id, ghsa_id)

    # other
    other = str(v)
    if re.search(cve_re, other):
        cves = re.findall(cve_re, other)
    elif re.search(rhsa_re, other):
        rhsas = re.findall(rhsa_re, other)
    elif re.search(ghsa_re, other):
        ghsas = re.findall(ghsa_re, other)

    # print("sas:", cves, rhsas, ghsas)

    if len(set(cves)) == 1:
        if cve_id == "":
            cve_id = cves[0]

    if len(set(rhsas)) == 1:
        if rhsa_id == "":
            rhsa_id = rhsas[0]

    if len(set(ghsas)) == 1:
        if ghsa_id == "":
            ghsa_id = ghsas[0]

    id = cve_id or rhsa_id or ghsa_id
    sas = [cve_id, rhsa_id, ghsa_id]
    sas.extend(cves)
    sas.extend(rhsas)
    sas.extend(ghsas)
    sas = set(sas)
    sas.discard("")
    sas = list(sas)
    # print(id, cve_id, sas)
    return id, cve_id, sas

In [11]:
def get_severity(v):
    severity = v.get("level")
    return severity

In [22]:
def get_package(v):
    package = v.get("locations")[0].get("message").get("text")
    package = package.split(": ")[1]
    return package

In [23]:
def get_distro(v):
    distro = v.get("distro").get("name")
    version = v.get("distro").get("version")
    return distro, version

In [24]:
def get_fixed(v):
    if v.get("fixes"):
        return True
    return False

In [25]:
error_tags = []
tags_with_res = {}
counter = 0
for tag in tags:
    tag_res = []
    tag_data = get_v(tag)
    if tag_data:
        for run in tag_data["runs"]:
            results = run["results"]
            rules = run["tool"]["driver"]["rules"]
            for v in results:
                rule_id = v["ruleId"]
                rule = next(r for r in rules if r["id"] == rule_id)

                id, cve_id, sas = get_cve_ids(v)
                # print(tag)
                # print(id)
                res = {
                    "id": id,
                    "cve_id": cve_id,
                    "sas": sas,
                    "severity": get_severity(v),
                    "package": get_package(v),
                    "distro": "",
                    "fixed": "",
                }
                if len(sas) > 0:
                    tag_res.append(res)
        tags_with_res[tag] = tag_res
    else:
        error_tags.append(tag)
    counter += 1
    if counter % 100 == 0:
        print(counter)

100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
mattermost/mattermost-team-edition:1d5b47a not exists
mattermost/mattermost-team-edition:5ce0c57 not exists
1800
1900
2000
2100
2200
2300
mprasil/bitwarden:latest not exists
2400
2500
2600
2700
kubernetes/pause:10.11.6-x86_64 not exists
kubernetes/pause:10.11.4 not exists
kubernetes/pause:10.11.2 not exists
2800
2900
minio/console:v0.15.2 not exists
minio/console:v0.26.1 not exists
minio/console:v0.17.1 not exists
3000
3100
3200


In [18]:
with open("../final_results/trivy_tags_vulns.json", "w") as f:
    json.dump(tags_with_res, f, indent=4)

In [19]:
tags_with_res_flat = []

for tag in tags_with_res:
    for cve in tags_with_res[tag]:
        cve["tag"] = tag
        tags_with_res_flat.append(cve)

In [20]:
with open("../final_results/trivy_tags_vulns_flat.json", "w") as f:
    json.dump(tags_with_res_flat, f, indent=4)

In [21]:
pd.DataFrame.from_dict(tags_with_res_flat[:10000]).to_clipboard(excel=True)